# setting up model

## model parameters

In [13]:
# optimal model for analyzing scaled load
# setting up the model
from pyomo.environ import *
import pandas as pd
import time
import json

big_M = 1e6
gas_price_value = 0.287               # price for gas, /MWh
gas_carbon = 0.4                      # gas carbon emission coefficient, unit: tons/MWh
carbon_emission_rate = 0.5366         # grid carbon emission coefficient, unit: tons/MWh

discount_rate = 0.06                  # discount rate

pv_rate = {1: 674.294, 2: 586.419, 3: 579.049, 4: 683.491}  # maximum photovoltaic generation per square kilometer for each city, unit: MW
sc_rate = {1: 3371.47, 2: 2932.09, 3: 2895.25, 4: 3417.45}  # maximum solar thermal generation per square kilometer for each city, unit: MW

#-----------------------------------------------------
# Device class definitions
# Photovoltaic/Solar thermal devices
class solar_device:
    def __init__(self, label, efficiency, output_kind, cost, area_rate):
        self.label = label              # device name
        self.efficiency = efficiency    # list, representing the efficiency of outputs for different energy types
        self.output_kind = output_kind  # list, representing the output energy types
        self.cost = cost                # construction cost per unit input capacity
        self.area_rate = area_rate      # generation/thermal output per unit area, unit: MW/m^2
        pass

# Energy conversion devices
class conversion_device:
    # Energy conversion device
    def __init__(self, label, efficiency, input_kind, output_kind, cost):
        # Record basic information about the device
        self.label = label              # device name
        self.efficiency = efficiency    # list, representing the efficiency of outputs for different energy types
        self.input_kind = input_kind    # string, representing the input energy type (currently supports single input type only)
        self.output_kind = output_kind  # list, representing the output energy types
        self.cost = cost                # construction cost per unit input capacity
        pass

class storage_device:
    # Energy storage device
    def __init__(self, label, input_efficiency, output_efficiency, input_kind,\
        output_kind, cost, self_discharge_rate, t_duration):
        self.label = label                          # device name
        self.input_efficiency = input_efficiency    # input efficiency
        self.output_efficiency = output_efficiency  # output efficiency
        self.input_kind = input_kind                # string, representing the input energy type
        self.output_kind = output_kind              # string, representing the output energy type
        self.cost = cost                            # construction cost per unit storage capacity
        self.self_discharge_rate = self_discharge_rate  # self-discharge rate
        self.t_duration = t_duration                # duration of the storage device cycle
        pass



## read and process the data

In [14]:
# read and process the data
#-----------------------------------------------------
def load_scaling(load, scale):
    load_scaled = [i * (1 + scale / 100) for i in load]
    return load_scaled

def read_data(city_code, load, scale):
    # Select the corresponding file name based on the input city code
    city_map = {
        1: "Beijing",
        3: "Wuhan",
        4: "Urumqi"
    }

    # Data file path
    file_path = './data/all_data.json'
    data = json.load(open(file_path, 'r'))
    # Read data
    elec_load = data[city_map[city_code]]["elec"]
    heat_load = data[city_map[city_code]]["heat"]
    cold_load = data[city_map[city_code]]["cool"]

    elec_price = data['elec_price']
    gas_price = [gas_price_value for _ in range(8760)]
    pv_I = data[city_map[city_code]]["pv"]
    elec_carbon = [carbon_emission_rate for _ in range(8760)]
    # Scale the data
    if load =='elec':
        elec_load = load_scaling(elec_load, scale)
    elif load == 'heat':
        heat_load = load_scaling(heat_load, scale)
    elif load == 'cool':
        cold_load = load_scaling(cold_load, scale)
    elif load == 'all':
        heat_load = load_scaling(heat_load, scale)
        cold_load = load_scaling(cold_load, scale)
    else:
        pass
    return elec_load, heat_load, cold_load, elec_price, gas_price , pv_I, elec_carbon

## optimization

In [15]:
# optimization function
# 折旧率计算函数
def old_equal(cost, year):
    return discount_rate/(1 - (1 + discount_rate) ** (-year))*cost

def optimal_plan(city_code, carbon_price, pv_space, load, scale):
    # 记录开始的时间
    start_time = time.time()
    print('Modeling...')
    #-----------------------------------------------------
    # 定义求解模型
    m = ConcreteModel()
    #-----------------------------------------------------
    # 首先将各个数据读入，并列表化。运行价格单位为元/MWh，在目标函数那边修正为万元/MWh
    elec_load, heat_load, cold_load, elec_price, gas_price, pv_I, elec_carbon = read_data(city_code, load, scale)
    m.elec_load = elec_load
    m.heat_load = heat_load
    m.cold_load = cold_load
    m.pv_I = pv_I                   # 光伏发电/太阳能集热器按最大值归一化后的比例
    
    m.elec_price = elec_price
    m.gas_price = gas_price
    
    m.elec_carbon = elec_carbon     # 电网碳排放系数
    
    m.carbon_price = carbon_price   # 碳排放价格
    
    m.pv_space = pv_space           # 可装太阳能的面积
    
    # 所有待规划设备的字典
    # 光伏发电/太阳能集热器
    pv = solar_device(label = "PV", efficiency=[0.85], output_kind = ["elec"], cost = old_equal(689835, 25), area_rate = 100)
    sc = solar_device(label = "SC", efficiency=[0.75], output_kind = ["heat"], cost = old_equal(131400, 20), area_rate = 500)
    m.solar_device_list = [pv, sc]
    
    # 各能量转换设备信息录入
    heat_elec_collab = conversion_device(label = "CHP", efficiency=[0.3, 0.65], \
                                        input_kind = "gas", output_kind = ["elec", "heat"], cost = old_equal(773.07, 30))

    elec_boiler = conversion_device(label = "Electric_Boiler", efficiency=[0.85], \
                                        input_kind = "elec", output_kind = ["heat"], cost = old_equal(55.48, 20))
    
    compress_cold = conversion_device(label = "CERG", efficiency=[3.5], \
                                        input_kind = "elec", output_kind = ["cold"], cost = old_equal(123.37, 15))
    
    absorb_cold = conversion_device(label = "WARP", efficiency=[1.2], \
                                        input_kind = "heat", output_kind = ["cold"], cost = old_equal(86.14, 20))
    
    gas_boilder = conversion_device(label = "Gas_Boiler", efficiency=[0.85], \
                                        input_kind = "gas", output_kind = ["heat"], cost = old_equal(44, 20))
    
    Ground_source_heat_pump_heat = conversion_device(label = "Ground_Heat_Pump_heat", efficiency=[3.4], \
                                        input_kind = "elec", output_kind = ["heat"], cost = old_equal(330, 20))
    Ground_source_heat_pump_cold = conversion_device(label = "Ground_Heat_Pump_cold", efficiency=[4.6], \
                                        input_kind = "elec", output_kind = ["cold"], cost = 0)
    
    m.conversion_device_list = [heat_elec_collab, elec_boiler,compress_cold,\
                            absorb_cold, gas_boilder, Ground_source_heat_pump_heat,\
                            Ground_source_heat_pump_cold]
    
    # 各储能设备信息录入
    elec_storage = storage_device(label = "Elec_Storage", input_efficiency = 0.9539, output_efficiency = 0.9539, \
                                input_kind = "elec", output_kind = "elec", cost = old_equal(228, 10), self_discharge_rate = 0.00054, t_duration = 2)
    heat_storage = storage_device(label = "Heat_Storage", input_efficiency = 0.894, output_efficiency = 0.894, \
                                input_kind = "heat", output_kind = "heat", cost = old_equal(11, 20), self_discharge_rate = 0.0075,  t_duration = 5)
    cold_storage = storage_device(label = "Cold_Storage", input_efficiency = 0.894, output_efficiency = 0.894, \
                                input_kind = "cold", output_kind = "cold", cost = old_equal(11, 20), self_discharge_rate = 0.0075,  t_duration = 5)
    Seasonal_Heat_Storage = storage_device(label = "Seasonal_Heat_Storage", input_efficiency = 1, output_efficiency = 1, \
                                input_kind = "heat", output_kind = "heat", cost = old_equal(1.1325, 20),  self_discharge_rate = 0, t_duration = 1)
    
    m.storage_device_list = [elec_storage, heat_storage, cold_storage, Seasonal_Heat_Storage]
    
    #-------------------------------------------------------------------
    # 定义时刻
    m.t_8760 = Set(initialize = [i for i in range(8760)])
    m.day_364 = Set(initialize = [i for i in range(364)])
    #----------------------------------------
    
    # 定义转换设备下标列表
    converter_power_index = []
    for device in m.conversion_device_list:
        # 输入能源种类
        device_kind_name = device.label + "_" + device.input_kind
        converter_power_index.append(device_kind_name)
        # 输出能源种类
        for output_kind in device.output_kind:
            device_kind_name = device.label + "_" + output_kind
            converter_power_index.append(device_kind_name)
    
    m.set_converter_power = Set(initialize = converter_power_index)
    m.set_converter = Set(initialize = range(len(m.conversion_device_list)))
    m.set_storage = Set(initialize = range(len(m.storage_device_list)))

    #----------------------------------------
    # 转换设备相关变量约束定义
    # 转换设备功率变量
    m.convert_invest = Var(m.set_converter, within = NonNegativeReals)
    m.convert_power = Var(m.set_converter_power, m.t_8760, within = NonNegativeReals)

    # 转换设备约束定义
    # 首先定义转换效率相关的约束
    for device in m.conversion_device_list:
        for output in device.output_kind:
            # 检索output在设备输出列表中的位置
            i = device.output_kind.index(output)
            # 正式定义约束
            fun_name = "c_{}_{}".format(device.label, output)
            input_kind = device.label + "_" + device.input_kind
            output_kind = device.label + "_" + output
            code_str = f'def {fun_name}(model, t):\n\t' \
                    f'return {device.efficiency[i]} * model.convert_power["{input_kind}",  t] == model.convert_power["{output_kind}", t]'
            
            local_env = {'m': m}
            exec(code_str, globals(), local_env)
            exec(f"m.constraint_{fun_name} = Constraint(m.t_8760, rule={fun_name})", globals(), local_env)
    
    # 然后定义设备输入容量上限
    def c_max_converter_input(model, device_id, t):
        m = model
        the_device = m.conversion_device_list[device_id]
        input_key = the_device.label + "_" + the_device.input_kind
        
        return m.convert_power[input_key, t] <= m.convert_invest[device_id]
    m.c_max_converter_input = Constraint(m.set_converter, m.t_8760, rule=c_max_converter_input)
    
    #----------------------------------------
    # 定义0-1变量，用于判断是否使用季节性热储能
    m.seasonal_heat_storage_used = Var(within=Binary)

    # 定义0-1变量，表示储能是充能还是放能
    m.Ground_source_heat_pump_heat_flag = Var(m.t_8760, within=Binary)
    m.Ground_source_heat_pump_cold_flag = Var(m.t_8760, within=Binary)
    
    # TODO: 设置长期储热的充放能时间，随月份变化约束
    
    
    
    # heat_pump的容量约束
    def c_Ground_source_heat_pump(model):
        m = model
        Ground_heat_pump_heat_index = next(i for i, device in enumerate(m.conversion_device_list) if device.label == "Ground_Heat_Pump_heat")
        Ground_heat_pump_cold_index = next(i for i, device in enumerate(m.conversion_device_list) if device.label == "Ground_Heat_Pump_cold")
        return m.convert_invest[Ground_heat_pump_heat_index] == m.convert_invest[Ground_heat_pump_cold_index]
    m.c_Ground_source_heat_pump = Constraint(rule=c_Ground_source_heat_pump)
        
    def c_Ground_source_heat_pump_heat_input(model, t):
        m = model
        return m.convert_power["Ground_Heat_Pump_heat_elec", t] <= m.Ground_source_heat_pump_heat_flag[t] * big_M
    m.c_Ground_source_heat_pump_input = Constraint(m.t_8760, rule=c_Ground_source_heat_pump_heat_input)
    
    def c_Ground_source_heat_pump_cold_input(model, t):
        m = model
        return m.convert_power["Ground_Heat_Pump_cold_elec", t] <= m.Ground_source_heat_pump_cold_flag[t] * big_M
    m.c_Ground_source_heat_pump_output = Constraint(m.t_8760, rule=c_Ground_source_heat_pump_cold_input)
    
    def c_Ground_source_heat_pump_mutual_exclusive(model, t):
        m = model
        return m.Ground_source_heat_pump_heat_flag[t] + m.Ground_source_heat_pump_cold_flag[t] <= 1
    m.c_Ground_source_heat_pump_mutual_exclusive = Constraint(m.t_8760, rule=c_Ground_source_heat_pump_mutual_exclusive)

#----------------------------------------
    m.storage_invest = Var(m.set_storage, within = NonNegativeReals)
    m.storage_charge_power = Var(m.set_storage,  m.t_8760, within = NonNegativeReals)
    m.storage_discharge_power = Var(m.set_storage,  m.t_8760, within = NonNegativeReals)
    m.storage_soc = Var(m.set_storage, m.t_8760, within = NonNegativeReals)

    # 季节性储能输入输出关联地源热泵
    # 季节性储热从热网额外接受的能量决策变量
    m.seasonal_heat_storage_heating = Var(m.t_8760, within = NonNegativeReals)
    
    # 输入与热泵制冷功率关联
    def c_seasonal_heat_storage_input(model, t):
        m = model
        seasonal_heat_storage_index = next(i for i, device in enumerate(m.storage_device_list) if device.label == "Seasonal_Heat_Storage")
        return m.storage_charge_power[seasonal_heat_storage_index, t] == (4.6 + 1) * m.convert_power["Ground_Heat_Pump_cold_elec", t] 
    m.c_seasonal_heat_storage_input = Constraint(m.t_8760, rule=c_seasonal_heat_storage_input)

    # 输出与热泵制热功率关联
    def c_seasonal_heat_storage_output(model, t):
        m = model
        seasonal_heat_storage_index = next(i for i, device in enumerate(m.storage_device_list) if device.label == "Seasonal_Heat_Storage")
        return m.storage_discharge_power[seasonal_heat_storage_index, t] == (3.4 - 1) * m.convert_power["Ground_Heat_Pump_heat_elec", t]
    m.c_seasonal_heat_storage_output = Constraint(m.t_8760, rule=c_seasonal_heat_storage_output)

    # 定义储存能量转移约束
    def c_storage_transfer(model, storage_id, t):
        m = model
        the_device = m.storage_device_list[storage_id]
        
        if the_device.label == "Seasonal_Heat_Storage":
            # 季节性储能
            if t == 0:
                return m.storage_soc[storage_id, 0] == m.storage_soc[storage_id, 8759] * (1 - the_device.self_discharge_rate)  \
                    + m.storage_charge_power[storage_id, 0] * the_device.input_efficiency \
                    - m.storage_discharge_power[storage_id, 0] / the_device.output_efficiency \
                    + m.seasonal_heat_storage_heating[0]
            else:
                return m.storage_soc[storage_id, t] == m.storage_soc[storage_id, t-1] * (1 - the_device.self_discharge_rate) \
                    + m.storage_charge_power[storage_id, t] * the_device.input_efficiency \
                    - m.storage_discharge_power[storage_id, t] / the_device.output_efficiency \
                    + m.seasonal_heat_storage_heating[t]
        else:
            # 非季节性储能
            if t == 0:
                return m.storage_soc[storage_id, 0] == m.storage_soc[storage_id, 8759] * (1 - the_device.self_discharge_rate)  \
                    + m.storage_charge_power[storage_id, 0] * the_device.input_efficiency \
                    - m.storage_discharge_power[storage_id, 0] / the_device.output_efficiency 
            else:
                return m.storage_soc[storage_id, t] == m.storage_soc[storage_id, t-1] * (1 - the_device.self_discharge_rate) \
                    + m.storage_charge_power[storage_id, t] * the_device.input_efficiency \
                    - m.storage_discharge_power[storage_id, t] / the_device.output_efficiency 
    m.c_storage_transfer = Constraint(m.set_storage, m.t_8760, rule = c_storage_transfer)
    
    # 短期储能日循环约束
    def c_storage_daily_cycle(model, storage_id, day):
        m = model
        the_device = m.storage_device_list[storage_id]
        # 季节性储能不需要这个约束
        if the_device.label == "Seasonal_Heat_Storage":
            return Constraint.Skip
        else:
            return m.storage_soc[storage_id, day * 24] == m.storage_soc[storage_id, (day + 1) * 24]
    m.c_storage_daily_cycle = Constraint(m.set_storage, m.day_364, rule = c_storage_daily_cycle)
    
    # 然后定义设备输入容量上限
    def c_max_storage_input(model, storage_id, t):
        m = model
        the_device = m.storage_device_list[storage_id]
        # 季节性储能不需要这个约束
        if the_device.label == "Seasonal_Heat_Storage":
            return Constraint.Skip
        else:
            return m.storage_charge_power[storage_id, t] <= m.storage_invest[storage_id] / the_device.t_duration
    m.c_max_storage_input = Constraint(m.set_storage, m.t_8760, rule=c_max_storage_input) 
    
    # 定义设备充放功率互斥约束
    #def c_storage_charge_flag(model, storage_id, t):
    #    m = model
    #    return m.storage_charge_power[storage_id, t] <= big_M * m.storage_charge_flag[storage_id, t]
    #m.c_storage_charge_flag = Constraint(m.set_storage, m.t_8760, rule = c_storage_charge_flag)
    
    def c_max_storage_output(model, storage_id,  t):
        m = model
        the_device = m.storage_device_list[storage_id]
        # 季节性储能不需要这个约束
        if the_device.label == "Seasonal_Heat_Storage":
            return Constraint.Skip
        else:
            return m.storage_discharge_power[storage_id, t] <= m.storage_invest[storage_id] / the_device.t_duration
    m.c_max_storage_output = Constraint(m.set_storage, m.t_8760, rule = c_max_storage_output)

    #def c_storage_discharge_flag(model, storage_id,  t):
    #    m = model
    #    return m.storage_discharge_power[storage_id, t] <= big_M * m.storage_discharge_flag[storage_id,  t]
    #m.c_storage_discharge_flag = Constraint(m.set_storage,  m.t_8760, rule = c_storage_discharge_flag)
    
    def c_max_storage_cap(model, storage_id,  t):
        m = model
        return m.storage_soc[storage_id, t] <= m.storage_invest[storage_id]
    m.c_max_storage_cap = Constraint(m.set_storage, m.t_8760, rule = c_max_storage_cap)
    
    #def c_mutual_exclusive(model, storage_id, t):
    #    m = model
    #    return m.storage_charge_flag[storage_id, t] + m.storage_discharge_flag[storage_id, t] <= 1
    #m.c_mutual_exclusive = Constraint(m.set_storage, m.t_8760, rule = c_mutual_exclusive)
    
    #----------------------------------------
    # 季节性储能是否投建的0-1约束
    def c_seasonal_heat_storage(model):
        m = model
        # 找到季节性热储能设备的索引
        for storage_id, device in enumerate(m.storage_device_list):
            if device.label == "Seasonal_Heat_Storage":
                return m.storage_invest[storage_id] <= big_M * m.seasonal_heat_storage_used
        return Constraint.Skip
    m.c_seasonal_heat_storage = Constraint(rule=c_seasonal_heat_storage)

    #----------------------------------------
    # 定义投资的光伏发电/太阳能集热器的约束
    m.solar_Area = Var(['pv', 'sc'], within=NonNegativeReals, initialize=0)
    def c_solar_invest(model):
        m = model
        return m.solar_Area['pv'] + m.solar_Area['sc'] <= m.pv_space
    m.c_solar_invest = Constraint(rule=c_solar_invest)
    
    # 能量母线约束
    # 首先定义能源类型
    m.set_energy_kind = Set(initialize=["elec", "heat", "cold", "gas"])
    m.set_buy_energy = Set(initialize=["elec", "gas"])
    m.set_solar_energy = Set(initialize=["elec", "heat"])
    # 定义购电的决策变量
    m.buy_energy = Var(m.set_buy_energy, m.t_8760, within = NonNegativeReals)
    # 定义光伏发电/太阳能集热量的决策变量
    m.solar_energy = Var(m.set_solar_energy, m.t_8760, within=NonNegativeReals)

    # 定义光伏发电和太阳能集热器的约束
    def c_solar_energy_elec(model, t):
        m = model
        return m.solar_energy["elec", t] <= m.solar_Area['pv'] * m.pv_I[t] * pv_rate[city_code]

    def c_solar_energy_heat(model, t):
        m = model
        return m.solar_energy["heat", t] <= m.solar_Area['sc'] * m.pv_I[t] * sc_rate[city_code]

    m.c_solar_energy_elec = Constraint(m.t_8760, rule=c_solar_energy_elec)
    m.c_solar_energy_heat = Constraint(m.t_8760, rule=c_solar_energy_heat)

    # 然后定义能源平衡约束
    def c_bus_balance(model, energy_kind, t):
        m = model
        # 首先定义总产能源的变量
        total_output = 0
        # 购电，看是否是气和电
        if energy_kind == "elec" or energy_kind == "gas":
            total_output += m.buy_energy[energy_kind, t]
        
        # 光伏发电或太阳能集热器
        if energy_kind == "elec":
            total_output += m.solar_energy["elec", t]
        elif energy_kind == "heat":
            total_output += m.solar_energy["heat", t]
        
        # 能源转换设备
        for device in m.conversion_device_list:
            if energy_kind == device.input_kind:
                input_key = device.label + "_" + energy_kind
                total_output -= m.convert_power[input_key, t]
            elif energy_kind in device.output_kind:
                output_key = device.label + "_" + energy_kind
                total_output += m.convert_power[output_key, t]
        
        # 储能设备
        for device_id in range(len(m.storage_device_list)):
            the_device = m.storage_device_list[device_id]
            # 跳过季节性热储，因为季节性热储从热泵那里接收和输出能量
            if the_device.label == "Seasonal_Heat_Storage":
                continue
            if energy_kind == the_device.input_kind:
                total_output += m.storage_discharge_power[device_id, t] - m.storage_charge_power[device_id, t]
        
        # 根据能源类型返回不同的约束
        if energy_kind == "elec":
            return total_output == m.elec_load[t]
        elif energy_kind == "heat":
            return total_output == m.heat_load[t] + m.seasonal_heat_storage_heating[t]
        elif energy_kind == "cold":
            return total_output == m.cold_load[t]
        elif energy_kind == "gas":
            return total_output == 0
        
    m.c_bus_balance = Constraint(m.set_energy_kind, m.t_8760, rule=c_bus_balance)
    #----------------------------------------
    # 然后计算运行成本
    # 定义目标函数
    m.total_cost = Var(within = NonNegativeReals)
    # 定义约束
    def c_objective(model):
        m = model
        #------------------------------------------------
        # 容量成本
        m.invest_cost = 0
        # 转换设备
        for device_id in range(len(m.conversion_device_list)):
            the_device = m.conversion_device_list[device_id]
            m.invest_cost += the_device.cost * m.convert_invest[device_id]
        # 储能设备
        for device_id in range(len(m.storage_device_list)):
            the_device = m.storage_device_list[device_id]
            if the_device.label == "Seasonal_Heat_Storage":
                m.invest_cost += old_equal(116.32436, 20) * m.seasonal_heat_storage_used + the_device.cost * m.storage_invest[device_id]
            else:
                m.invest_cost += the_device.cost * m.storage_invest[device_id]
        # 光伏发电/太阳能集热器
        m.invest_cost += pv.cost * m.solar_Area['pv']
        m.invest_cost += sc.cost * m.solar_Area['sc']
        #------------------------------------------------
        # 运行成本
        m.oper_cost = 0
        m.carbon_cost = 0
        for t in m.t_8760:
            # 统一为万元单位
            # 购电成本
            m.oper_cost += m.elec_price[t] * m.buy_energy["elec", t] / 10000
            m.oper_cost += m.gas_price[t] * m.buy_energy["gas", t] / 10000
            # 碳排放成本
            m.carbon_cost += m.carbon_price * m.elec_carbon[t] * m.buy_energy["elec", t] / 10000
            m.carbon_cost += m.carbon_price * gas_carbon * m.buy_energy["gas", t] / 10000

        # 全年运行成本
        return m.total_cost == m.invest_cost + m.oper_cost + m.carbon_cost
    m.c_objective = Constraint(rule = c_objective)

    # 定义目标函数
    m.objective = Objective(expr = m.total_cost, sense = minimize)

    #----------------------------------------
    # 求解
    print('Construction Complete. {}s used. Optimizing...'.format(time.time()-start_time))
    start_time = time.time()
    opt = SolverFactory('gurobi') 
    opt.solve(m)
    print('Optimization Complete. {}s used.'.format(time.time()-start_time))

    return m



# scaling the load between -5% to 5%

In [16]:
#定义一个获取季节性热储容量的函数
def get_seasonal_heat_storage_capacity(m):
    for device in m.set_storage: 
        if m.storage_device_list[device].label == 'Seasonal_Heat_Storage':
            return m.storage_invest[device]()
    return 0

In [17]:
#beijing
#+1%
m1_beijing = optimal_plan(1, 100, 3.8, 'all', 1)
#-1%
m_1_beijing = optimal_plan(1, 100, 3.8, 'all', -1)

#+2%
m2_beijing = optimal_plan(1, 100, 3.8, 'all', 2)
#-2%
m_2_beijing = optimal_plan(1, 100, 3.8, 'all', -2)

#+3%
m3_beijing = optimal_plan(1, 100, 3.8, 'all', 3)
#-3%
m_3_beijing = optimal_plan(1, 100, 3.8, 'all', -3)

#+4%
m4_beijing = optimal_plan(1, 100, 3.8, 'all', 4)
#-4%
m_4_beijing = optimal_plan(1, 100, 3.8, 'all', -4)
#+5%
m5_beijing = optimal_plan(1, 100, 3.8, 'all', 5)
#-5%
m_5_beijing = optimal_plan(1, 100, 3.8, 'all', -5)

#0
m0_beijing = optimal_plan(1, 100, 3.8, 'all', 0)

Modeling...
Construction Complete. 3.3788115978240967s used. Optimizing...
Optimization Complete. 148.8321557044983s used.
Modeling...
Construction Complete. 2.8591785430908203s used. Optimizing...
Optimization Complete. 83.6609411239624s used.
Modeling...
Construction Complete. 2.7194623947143555s used. Optimizing...
Optimization Complete. 155.59745168685913s used.
Modeling...
Construction Complete. 3.0017337799072266s used. Optimizing...
Optimization Complete. 157.6421844959259s used.
Modeling...
Construction Complete. 3.1871776580810547s used. Optimizing...
Optimization Complete. 131.3895285129547s used.
Modeling...
Construction Complete. 2.227731704711914s used. Optimizing...
Optimization Complete. 90.72377443313599s used.
Modeling...
Construction Complete. 2.215333938598633s used. Optimizing...
Optimization Complete. 141.23112392425537s used.
Modeling...
Construction Complete. 3.7211556434631348s used. Optimizing...
Optimization Complete. 128.76183009147644s used.
Modeling...
Cons

In [18]:
#Wuhan


#+1%
m1_wuhan = optimal_plan(3, 100, 3.8, 'all', 1)
#-1%
m_1_wuhan = optimal_plan(3, 100, 3.8, 'all', -1)
#+2%
m2_wuhan = optimal_plan(3, 100, 3.8, 'all', 2)
#-2%
m_2_wuhan = optimal_plan(3, 100, 3.8, 'all', -2)
#+3%
m3_wuhan = optimal_plan(3, 100, 3.8, 'all', 3)
#-3%
m_3_wuhan = optimal_plan(3, 100, 3.8, 'all', -3)
#+4%
m4_wuhan = optimal_plan(3, 100, 3.8, 'all', 4)
#-4%
m_4_wuhan = optimal_plan(3, 100, 3.8, 'all', -4)
#+5%
m5_wuhan = optimal_plan(3, 100, 3.8, 'all', 5)
#-5%
m_5_wuhan = optimal_plan(3, 100, 3.8, 'all', -5)
#0
m0_wuhan = optimal_plan(3, 100, 3.8, 'all', 0)

Modeling...
Construction Complete. 4.5606958866119385s used. Optimizing...
Optimization Complete. 226.29658150672913s used.
Modeling...
Construction Complete. 2.268465757369995s used. Optimizing...
Optimization Complete. 258.60711765289307s used.
Modeling...
Construction Complete. 2.221353530883789s used. Optimizing...
Optimization Complete. 251.11017513275146s used.
Modeling...
Construction Complete. 5.222293853759766s used. Optimizing...
Optimization Complete. 265.32556200027466s used.
Modeling...
Construction Complete. 2.335629463195801s used. Optimizing...
Optimization Complete. 421.88683009147644s used.
Modeling...
Construction Complete. 2.19500470161438s used. Optimizing...
Optimization Complete. 284.9890134334564s used.
Modeling...
Construction Complete. 2.2198071479797363s used. Optimizing...
Optimization Complete. 296.59660482406616s used.
Modeling...
Construction Complete. 5.8760986328125s used. Optimizing...
Optimization Complete. 263.1938190460205s used.
Modeling...
Constru

In [19]:
# Urumqi


#+1%
m1_urumqi = optimal_plan(4, 100, 3.8, 'all', 1)
#-1%
m_1_urumqi = optimal_plan(4, 100, 3.8, 'all', -1)
#+2%
m2_urumqi = optimal_plan(4, 100, 3.8, 'all', 2)
#-2%
m_2_urumqi = optimal_plan(4, 100, 3.8, 'all', -2)
#+3%
m3_urumqi = optimal_plan(4, 100, 3.8, 'all', 3)
#-3%
m_3_urumqi = optimal_plan(4, 100, 3.8, 'all', -3)
#+4%
m4_urumqi = optimal_plan(4, 100, 3.8, 'all', 4)
#-4%
m_4_urumqi = optimal_plan(4, 100, 3.8, 'all', -4)
#+5%
m5_urumqi = optimal_plan(4, 100, 3.8, 'all', 5)
#-5%
m_5_urumqi = optimal_plan(4, 100, 3.8, 'all', -5)
#0
m0_urumqi = optimal_plan(4, 100, 3.8, 'all', 0)


Modeling...
Construction Complete. 7.435733795166016s used. Optimizing...
Optimization Complete. 412.368803024292s used.
Modeling...
Construction Complete. 2.198483943939209s used. Optimizing...
Optimization Complete. 121.59908676147461s used.
Modeling...
Construction Complete. 2.313302516937256s used. Optimizing...
Optimization Complete. 127.79908728599548s used.
Modeling...
Construction Complete. 2.298041582107544s used. Optimizing...
Optimization Complete. 398.64984130859375s used.
Modeling...
Construction Complete. 3.45306134223938s used. Optimizing...
Optimization Complete. 719.2821300029755s used.
Modeling...
Construction Complete. 11.615542888641357s used. Optimizing...
Optimization Complete. 458.09234142303467s used.
Modeling...
Construction Complete. 2.8440568447113037s used. Optimizing...
Optimization Complete. 289.43749141693115s used.
Modeling...
Construction Complete. 3.8181474208831787s used. Optimizing...
Optimization Complete. 406.6427233219147s used.
Modeling...
Constr

In [ ]:
beijing_seasonal_heat_storage = [get_seasonal_heat_storage_capacity(m_5_beijing),
                                 get_seasonal_heat_storage_capacity(m_4_beijing),
                                 get_seasonal_heat_storage_capacity(m_3_beijing),
                                 get_seasonal_heat_storage_capacity(m_2_beijing),
                                 get_seasonal_heat_storage_capacity(m_1_beijing),
                                 get_seasonal_heat_storage_capacity(m0_beijing),
                                    get_seasonal_heat_storage_capacity(m1_beijing),
                                    get_seasonal_heat_storage_capacity(m2_beijing),
                                    get_seasonal_heat_storage_capacity(m3_beijing),
                                    get_seasonal_heat_storage_capacity(m4_beijing),
                                    get_seasonal_heat_storage_capacity(m5_beijing)]

wuhan_seasonal_heat_storage = [get_seasonal_heat_storage_capacity(m_5_wuhan),
                               get_seasonal_heat_storage_capacity(m_4_wuhan),
                               get_seasonal_heat_storage_capacity(m_3_wuhan),
                               get_seasonal_heat_storage_capacity(m_2_wuhan),
                               get_seasonal_heat_storage_capacity(m_1_wuhan),
                               get_seasonal_heat_storage_capacity(m0_wuhan),
                               get_seasonal_heat_storage_capacity(m1_wuhan),
                               get_seasonal_heat_storage_capacity(m2_wuhan),
                               get_seasonal_heat_storage_capacity(m3_wuhan),
                               get_seasonal_heat_storage_capacity(m4_wuhan),
                               get_seasonal_heat_storage_capacity(m5_wuhan)]

urumqi_seasonal_heat_storage = [get_seasonal_heat_storage_capacity(m_5_urumqi),
                                  get_seasonal_heat_storage_capacity(m_4_urumqi),
                                  get_seasonal_heat_storage_capacity(m_3_urumqi),
                                  get_seasonal_heat_storage_capacity(m_2_urumqi),
                                  get_seasonal_heat_storage_capacity(m_1_urumqi),
                                  get_seasonal_heat_storage_capacity(m0_urumqi),
                                  get_seasonal_heat_storage_capacity(m1_urumqi),
                                  get_seasonal_heat_storage_capacity(m2_urumqi),
                                  get_seasonal_heat_storage_capacity(m3_urumqi),
                                  get_seasonal_heat_storage_capacity(m4_urumqi),
                                  get_seasonal_heat_storage_capacity(m5_urumqi)]
#save the results to csv 
beijing_seasonal_heat_storage = pd.DataFrame(beijing_seasonal_heat_storage)
wuhan_seasonal_heat_storage = pd.DataFrame(wuhan_seasonal_heat_storage)
urumqi_seasonal_heat_storage = pd.DataFrame(urumqi_seasonal_heat_storage)
beijing_seasonal_heat_storage.to_csv('/home/user/workspaces/CUE2025_final/scaling_results/beijing_seasonal_heat_storage.csv', index=False)
wuhan_seasonal_heat_storage.to_csv('/home/user/workspaces/CUE2025_final/scaling_results/wuhan_seasonal_heat_storage.csv', index=False)
urumqi_seasonal_heat_storage.to_csv('/home/user/workspaces/CUE2025_final/scaling_results/urumqi_seasonal_heat_storage.csv', index=False)



In [28]:

beijing_seasonal_heat_storage = np.array(beijing_seasonal_heat_storage)
wuhan_seasonal_heat_storage = np.array(wuhan_seasonal_heat_storage)
urumqi_seasonal_heat_storage = np.array(urumqi_seasonal_heat_storage)
#

## Absolute change

In [29]:
import matplotlib.pyplot as plt

# Calculate absolute change
def calculate_absolute_change(data, base_value):
    return [(x - base_value) for x in data]

# Base values
base_value_beijing = beijing_seasonal_heat_storage[5][0]
base_value_wuhan = wuhan_seasonal_heat_storage[5][0]
base_value_urumqi = urumqi_seasonal_heat_storage[5][0]

# Calculate absolute changes
beijing_absolute = calculate_absolute_change(beijing_seasonal_heat_storage, base_value_beijing)
wuhan_absolute = calculate_absolute_change(wuhan_seasonal_heat_storage, base_value_wuhan)
urumqi_absolute = calculate_absolute_change(urumqi_seasonal_heat_storage, base_value_urumqi)

# Determine y-axis range (including all points)
x_values = [-5, -4, -3, -2, -1, 0, 1, 2, 3, 4, 5]
all_values = (
    beijing_absolute +
    wuhan_absolute +
    urumqi_absolute
)
y_min, y_max = min(all_values), max(all_values)

# Slightly expand the y-axis range
y_margin = (y_max - y_min) * 0.1  # Add a 10% margin
y_min -= y_margin
y_max += y_margin

# Plot
plt.figure(figsize=(20, 12), dpi=600)

# Beijing
plt.plot(x_values, beijing_absolute, label='Beijing', marker='o', markersize=20, linewidth=4, color='tab:orange')
# Wuhan
plt.plot(x_values, wuhan_absolute, label='Wuhan', marker='^', markersize=20, linewidth=4, color='tab:olive')
# Urumqi
plt.plot(x_values, urumqi_absolute, label='Urumqi', marker='d', markersize=20, linewidth=4, color='tab:purple')

# Set labels and title
plt.xlabel('Scaling Factor for \nHeating and Cooling Demand (%)', fontsize=40)
plt.ylabel('STES Capacity Change (MWh)', fontsize=40)

# Set y-axis range
plt.ylim(y_min, y_max)

# Set x-axis ticks
plt.xticks(ticks=[-5, -4, -3, -2, -1, 0, 1, 2, 3, 4, 5], fontsize=40)

# Legend in the bottom right of the plot
plt.legend(fontsize=40)

# Grid
plt.grid(True, linestyle='--', linewidth=0.5)

# Set tick font size
plt.yticks(fontsize=40)

# Adjust layout
plt.tight_layout()

# Show the plot
plt.show()

# Save the plot
plt.savefig('/home/user/workspaces/CUE2025_final/scaling_results/seasonal_heat_storage_scaling.png', dpi=600, bbox_inches='tight')

<Figure size 640x480 with 0 Axes>

## relative % change

In [2]:
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
beijing_seasonal_heat_storage = pd.read_csv('/home/user/workspaces/CUE2025_final/scaling_results/beijing_seasonal_heat_storage.csv')
wuhan_seasonal_heat_storage = pd.read_csv('/home/user/workspaces/CUE2025_final/scaling_results/wuhan_seasonal_heat_storage.csv')
urumqi_seasonal_heat_storage = pd.read_csv('/home/user/workspaces/CUE2025_final/scaling_results/urumqi_seasonal_heat_storage.csv')
beijing_seasonal_heat_storage = np.array(beijing_seasonal_heat_storage)
wuhan_seasonal_heat_storage = np.array(wuhan_seasonal_heat_storage)
urumqi_seasonal_heat_storage = np.array(urumqi_seasonal_heat_storage)


# Calculate relative percentage change
def calculate_relative_change(data, base_value):
    return [(x - base_value) / base_value * 100 if base_value != 0 else 0 for x in data]

# Base values for each city (corresponding to the point where scale factor = 0)
base_value_beijing = beijing_seasonal_heat_storage[5]
base_value_wuhan = wuhan_seasonal_heat_storage[5]
base_value_urumqi = urumqi_seasonal_heat_storage[5]

# Calculate relative percentage changes
beijing_relative = calculate_relative_change(beijing_seasonal_heat_storage, base_value_beijing)
wuhan_relative = calculate_relative_change(wuhan_seasonal_heat_storage, base_value_wuhan)
urumqi_relative = calculate_relative_change(urumqi_seasonal_heat_storage, base_value_urumqi)

# Define x-axis values
x_values = [-5, -4, -3, -2, -1, 0, 1, 2, 3, 4, 5]

# Determine y-axis range (including all points)
all_values = (
    beijing_relative +
    wuhan_relative +
    urumqi_relative
)
y_min, y_max = min(all_values), max(all_values)

# Slightly expand the y-axis range
y_margin = (y_max - y_min) * 0.1  # Add a 10% margin
y_min -= y_margin
y_max += y_margin

# Plot
plt.figure(figsize=(20, 12), dpi=600)

# Beijing
plt.plot(x_values, beijing_relative, label='Beijing', marker='o', markersize=20, linewidth=4, color='tab:orange')
# Wuhan
plt.plot(x_values, wuhan_relative, label='Wuhan', marker='^', markersize=20, linewidth=4, color='tab:olive')
# Urumqi
plt.plot(x_values, urumqi_relative, label='Urumqi', marker='d', markersize=20, linewidth=4, color='tab:purple')

# Set labels and title
plt.xlabel('Scaling Factor for \nHeat and Cooling Demand (%)', fontsize=40)
plt.ylabel('STES Capacity Relative Change (%)', fontsize=40)

# Set y-axis range
plt.ylim(y_min, y_max)

# Set x-axis ticks
plt.xticks(ticks=[-5, -4, -3, -2, -1, 0, 1, 2, 3, 4, 5], fontsize=40)

# Set y-axis tick font size
plt.yticks(fontsize=40)

# Place legend at the bottom
plt.legend(fontsize=40)

# Add grid
plt.grid(True, linestyle='--', linewidth=0.5)

# Adjust layout
plt.tight_layout()

# Show the plot
plt.show()

# Save the plot
plt.savefig('/home/user/workspaces/CUE2025_final/scaling_results/seasonal_heat_storage_capacity_relative_change.png', dpi=600)

<Figure size 640x480 with 0 Axes>

In [37]:
#boilers capacity
#beijing
def get_EB_capacity(m):
    for device in m.set_converter: 
        if m.conversion_device_list[device].label == 'Electric_Boiler':
            return m.convert_invest[device]()
    return 0
def get_GB_capacity(m):
    for device in m.set_converter: 
        if m.conversion_device_list[device].label == 'Gas_Boiler':
            return m.convert_invest[device]()
    return 0
cap =get_EB_capacity(m_1_beijing)+get_GB_capacity(m_1_beijing)
print('beijing 5% EB and GB capacity:', cap)
cap =get_EB_capacity(m5_beijing)+get_GB_capacity(m5_beijing)
print('beijing 5% EB and GB capacity:', cap)


beijing 5% EB and GB capacity: 57.38622134240252
beijing 5% EB and GB capacity: 70.1119463345492
